In [1]:
import os
import pathlib
from adtoolbox import core,configs,utils
import pandas as pd
db=core.Database(config=configs.Database())
#db.download_qiime_classifier_db() # downloads the qiime classifier if not already installed (only needs to download once)
metadata=pd.read_table("/Users/parsaghadermarzi/Desktop/Academics/Projects/Anaerobic_Digestion_Modeling/16s_study/wastewater_16s.csv",delimiter=",")
accessions=metadata["Run"].to_list()
metag_class=core.Metagenomics(configs.Metagenomics())
alignment_to_gtdb={}
base=pathlib.Path(os.path.join(core.Main_Dir,"sra_wastewater")) # base directory
for i in accessions:
    mg_config=configs.Metagenomics(top_repseq_dir=str(base/i/"seqs"/i/"dna-sequences.fasta"),
                                   vsearch_similarity=0.90,
                                   align_to_gtdb_outputs_dir=str(base/i/"seqs"/i))
    
    mg=core.Metagenomics(mg_config)
    command=mg.align_to_gtdb(container="None")
    os.system(command)
    alignment_to_gtdb[i]=mg.get_genomes_from_gtdb_alignment(save=False)


vsearch v2.22.1_macos_aarch64, 16.0GB RAM, 8 cores
https://github.com/torognes/vsearch

Reading file Database/Amplicon2GenomeDBs/ssu_all_r214.fna 100%
880725430 nt in 708813 seqs, min 200, max 6015, avg 1243
Masking 100%
Counting k-mers 100%
Creating k-mer index 100%
Searching 100%
Matching unique query sequences: 60 of 70 (85.71%)
vsearch v2.22.1_macos_aarch64, 16.0GB RAM, 8 cores
https://github.com/torognes/vsearch

Reading file Database/Amplicon2GenomeDBs/ssu_all_r214.fna 100%
880725430 nt in 708813 seqs, min 200, max 6015, avg 1243
Masking 100%
Counting k-mers 100%
Creating k-mer index 100%
Searching 100%
Matching unique query sequences: 62 of 73 (84.93%)
vsearch v2.22.1_macos_aarch64, 16.0GB RAM, 8 cores
https://github.com/torognes/vsearch

Reading file Database/Amplicon2GenomeDBs/ssu_all_r214.fna 100%
880725430 nt in 708813 seqs, min 200, max 6015, avg 1243
Masking 100%
Counting k-mers 100%
Creating k-mer index 100%
Searching 100%
Matching unique query sequences: 50 of 62 (80.65%

In [3]:
genome_ids=set()
for sample in alignment_to_gtdb:
    genome_ids.update(tuple(alignment_to_gtdb[sample].values()))
mg_config=configs.Metagenomics(genomes_base_dir=os.path.join(core.Main_Dir,"genomes"))
mg=core.Metagenomics(mg_config)
genome_address=mg.extract_genome_info(save=False)

In [5]:
for gid in genome_ids:
    if gid in genome_address:
        continue
    os.system(mg.download_genome(gid))


Warning Notice!

You are accessing a U.S. Government information system which includes this
computer, network, and all attached devices. This system is for
Government-authorized use only. Unauthorized use of this system may result in
disciplinary action and civil and criminal penalties. System users have no
expectation of privacy regarding any communications or data processed by this
system. At any time, the government may monitor, record, or seize any
communication or data transiting or stored on this information system.

-------------------------------------------------------------------------------

Welcome to the NCBI rsync server.


receiving file list ... 
31 files to consider
created directory ./genomes/GCF902374565.1~NZCABKQM010000006.1
565/
565/GCF_902374565.1_MGYG-HGUT-01389/
565/GCF_902374565.1_MGYG-HGUT-01389/GCF_902374565.1_MGYG-HGUT-01389_assembly_report.txt
        1888 100%    1.80MB/s    0:00:00 (xfer#1, to-check=28/31)
565/GCF_902374565.1_MGYG-HGUT-01389/GCF_90237456

In [10]:
mg.config.genomes_json_info=os.path.join(core.Main_Dir,"sra_wastewater","genome_address.json")
genome_address=mg.extract_genome_info(save=False)
genome_address={k:v for k,v in genome_address.items() if k in genome_ids}
mg=core.Metagenomics(configs.Metagenomics(genome_alignment_output=os.path.join(core.Main_Dir,"genomes")
                                          ,genomes_base_dir=os.path.join(core.Main_Dir,"genomes")))
for i in enumerate(genome_address):
        os.system(mg.align_genome_to_protein_db(genome_address[i[1]],i[1],container="None")[0])


Create directory tmp
easy-search /Users/parsaghadermarzi/Desktop/Academics/Projects/Anaerobic_Digestion_Modeling/16s_study/genomes/GCA024397005.1~JAJDMT010000065.1/005/GCA_024397005.1_ASM2439700v1/GCA_024397005.1_ASM2439700v1_genomic.fna.gz ./Database/Protein_DB.fasta ./genomes/Alignment_Results_mmseq_GCA024397005.1~JAJDMT010000065.1.tsv tmp --format-mode 4 

MMseqs Version:                        	14-7e284
Substitution matrix                    	aa:blosum62.out,nucl:nucleotide.out
Add backtrace                          	false
Alignment mode                         	3
Alignment mode                         	0
Allow wrapped scoring                  	false
E-value threshold                      	0.001
Seq. id. threshold                     	0
Min alignment length                   	0
Seq. id. mode                          	0
Alternative alignments                 	0
Coverage threshold                     	0
Coverage mode                          	0
Max sequence length                    

In [15]:
base=pathlib.Path(os.path.join(core.Main_Dir))

In [44]:
alf=list(base.rglob("Alignment_Results_mmseq_*.tsv"))
genome_cod={}
for i in alf:
    alignment_address=i
    ecs=mg.extract_ec_from_alignment(alignment_address,save=False)
    cods=mg.get_cod_from_ec_counts(ecs,save=False)
    genome_cod.update({i.name.rstrip(".tsv"):cods})
    print(i,flush=True)

genomes/Alignment_Results_mmseq_GCA002344125.1~DDTQ01000011.1.tsv
genomes/Alignment_Results_mmseq_GCA017983595.1~JAGOBC010000005.1.tsv
genomes/Alignment_Results_mmseq_GCF001886875.1~NZCP013239.1-#11.tsv
genomes/Alignment_Results_mmseq_GCA905211195.1~CAJLZS010000010.1.tsv
genomes/Alignment_Results_mmseq_GCA021155145.1~JAJNPX010000541.1.tsv
genomes/Alignment_Results_mmseq_GCA020532105.1~JAJBBI010000134.1.tsv
genomes/Alignment_Results_mmseq_GCF002777255.1~NZCP017634.1.tsv
genomes/Alignment_Results_mmseq_GCF009469765.1~NZSSSQ01000027.1.tsv
genomes/Alignment_Results_mmseq_GCA928721945.1~CAKMWB010000001.1.tsv
genomes/Alignment_Results_mmseq_GCA019136575.1~JAGVTX010000108.1.tsv
genomes/Alignment_Results_mmseq_GCA003963305.1~RXJR01000021.1.tsv
genomes/Alignment_Results_mmseq_GCF002978245.1~NZNRMR01000156.1.tsv
genomes/Alignment_Results_mmseq_GCA016703135.1~JADJCQ010000001.1.tsv
genomes/Alignment_Results_mmseq_GCF020089545.1~NZJAIRBK010000049.1.tsv
genomes/Alignment_Results_mmseq_GCF002995785.1

In [45]:
genome_cod

{'Alignment_Results_mmseq_GCA002344125.1~DDTQ01000011.1': {'X_ch': 1,
  'X_pr': 2,
  'X_li': 0,
  'X_su': 2,
  'X_aa': 4,
  'X_fa': 4,
  'X_ac_et': 2,
  'X_ac_lac': 2,
  'X_chain_et': 2,
  'X_chain_lac': 2,
  'X_VFA_deg': 0,
  'X_Me_ac': 0,
  'X_Me_CO2': 0,
  'X_et': 2,
  'X_lac': 2},
 'Alignment_Results_mmseq_GCA017983595.1~JAGOBC010000005.1': {'X_ch': 0,
  'X_pr': 5,
  'X_li': 0,
  'X_su': 5,
  'X_aa': 8,
  'X_fa': 12,
  'X_ac_et': 5,
  'X_ac_lac': 5,
  'X_chain_et': 5,
  'X_chain_lac': 5,
  'X_VFA_deg': 0,
  'X_Me_ac': 0,
  'X_Me_CO2': 0,
  'X_et': 5,
  'X_lac': 5},
 'Alignment_Results_mmseq_GCF001886875.1~NZCP013239.1-#11': {'X_ch': 0,
  'X_pr': 0,
  'X_li': 0,
  'X_su': 1,
  'X_aa': 2,
  'X_fa': 0,
  'X_ac_et': 0,
  'X_ac_lac': 1,
  'X_chain_et': 0,
  'X_chain_lac': 1,
  'X_VFA_deg': 0,
  'X_Me_ac': 0,
  'X_Me_CO2': 0,
  'X_et': 0,
  'X_lac': 1},
 'Alignment_Results_mmseq_GCA905211195.1~CAJLZS010000010.1': {'X_ch': 4,
  'X_pr': 10,
  'X_li': 0,
  'X_su': 4,
  'X_aa': 7,
  'X_fa': 

In [69]:
normalized_cods={}
samples=pathlib.Path(os.path.join(core.Main_Dir,"sra_wastewater"))
for i in samples.iterdir():
    sample_basedir=i/"seqs"/i.name
    if "SRR" in i.name:
        feature_table=pd.read_table(sample_basedir/"feature-table.tsv",delimiter="\t",skiprows=1)
        matches_table=pd.read_table(sample_basedir/"matches.blast",delimiter="\t",header=None)
        genome_map=dict(zip(matches_table[0],matches_table[1]))
        feature_table["#OTU ID"]=feature_table["#OTU ID"].apply(lambda x:genome_map.get(x,x))
        total_sum=feature_table.iloc[:,1].sum()
        feature_table[i.name]=feature_table[i.name]/total_sum
        assigned=feature_table[feature_table["#OTU ID"].str.contains("_")]
        jhkhkh=[]
        for genome_ in zip(assigned["#OTU ID"].apply(lambda x:"".join(x.split("_")[1:])),assigned[i.name]):
            if ("Alignment_Results_mmseq_"+genome_[0]) not in genome_cod.keys():
                genome_cod["Alignment_Results_mmseq_"+genome_[0]]={'X_ch':0,'X_pr':0,'X_li':0,'X_su':0,'X_aa':0,'X_fa':0,'X_ac_et':0,'X_ac_lac':0,'X_chain_et':0,'X_chain_lac':0,'X_VFA_deg':0,'X_Me_ac':0,'X_Me_CO2':0,'X_et':0,'X_lac':0,}
            jhkhkh.append({i:genome_cod["Alignment_Results_mmseq_"+genome_[0]][i]*genome_[1] for i in genome_cod["Alignment_Results_mmseq_"+genome_[0]]})
        total_sample_cod=pd.DataFrame(jhkhkh).sum()
        total_sample_cod=total_sample_cod.div(total_sample_cod.sum())
        normalized_cods[i.name]=total_sample_cod.to_dict()
    else:
        continue

In [70]:
normalized_cods

{'SRR19159482': {'X_ch': 0.0678651270207852,
  'X_pr': 0.054067436489607386,
  'X_li': 0.001888221709006928,
  'X_su': 0.078259584295612,
  'X_aa': 0.18715565819861435,
  'X_fa': 0.132105311778291,
  'X_ac_et': 0.07681108545034641,
  'X_ac_lac': 0.08910115473441108,
  'X_chain_et': 0.07133856812933026,
  'X_chain_lac': 0.08362863741339491,
  'X_VFA_deg': 0.0,
  'X_Me_ac': 0.0024277136258660506,
  'X_Me_CO2': 0.00030669745958429557,
  'X_et': 0.07133856812933026,
  'X_lac': 0.08370623556581985},
 'SRR19159476': {'X_ch': 0.08264441768274827,
  'X_pr': 0.080495560981447,
  'X_li': 0.00219213935997678,
  'X_su': 0.07939058016584895,
  'X_aa': 0.1888015031812754,
  'X_fa': 0.1443833112252302,
  'X_ac_et': 0.06449879954273142,
  'X_ac_lac': 0.08323509867173157,
  'X_chain_et': 0.05808023586502938,
  'X_chain_lac': 0.07681653499402952,
  'X_VFA_deg': 0.0,
  'X_Me_ac': 0.0014537881237476668,
  'X_Me_CO2': 0.0019477196403974873,
  'X_et': 0.05808023586502938,
  'X_lac': 0.07798007470077678},
 '

In [43]:
genome_cod["Alignment_Results_mmseq_"+genome_[0]]

{'X_ch': 0,
 'X_pr': 0,
 'X_li': 0,
 'X_su': 0,
 'X_aa': 0,
 'X_fa': 0,
 'X_ac_et': 0,
 'X_ac_lac': 0,
 'X_chain_et': 0,
 'X_chain_lac': 0,
 'X_VFA_deg': 0,
 'X_Me_ac': 1,
 'X_Me_CO2': 0,
 'X_et': 0,
 'X_lac': 0,
 'Alignment_Results_mmseq_GCA023457455.1~JAEWLR010000042.1': {'X_ch': 0,
  'X_pr': 0,
  'X_li': 0,
  'X_su': 0,
  'X_aa': 0,
  'X_fa': 0,
  'X_ac_et': 0,
  'X_ac_lac': 0,
  'X_chain_et': 0,
  'X_chain_lac': 0,
  'X_VFA_deg': 0,
  'X_Me_ac': 0,
  'X_Me_CO2': 0,
  'X_et': 0,
  'X_lac': 0},
 'Alignment_Results_mmseq_GCA024397005.1~JAJDMT010000065.1': {'X_ch': 0,
  'X_pr': 0,
  'X_li': 0,
  'X_su': 0,
  'X_aa': 0,
  'X_fa': 0,
  'X_ac_et': 0,
  'X_ac_lac': 0,
  'X_chain_et': 0,
  'X_chain_lac': 0,
  'X_VFA_deg': 0,
  'X_Me_ac': 0,
  'X_Me_CO2': 0,
  'X_et': 0,
  'X_lac': 0},
 'Alignment_Results_mmseq_GCF002193355.1~NZNHQF01000083.1': {'X_ch': 0,
  'X_pr': 0,
  'X_li': 0,
  'X_su': 0,
  'X_aa': 0,
  'X_fa': 0,
  'X_ac_et': 0,
  'X_ac_lac': 0,
  'X_chain_et': 0,
  'X_chain_lac': 0,


In [49]:
import json
with open("normalized_cods.json","w") as f:
    json.dump(normalized_cods,f)

In [71]:
metadata=pd.read_table("/Users/parsaghadermarzi/Desktop/Academics/Projects/Anaerobic_Digestion_Modeling/16s_study/wastewater_16s.csv",delimiter=",")

def format_for_report(cod_dict: dict, addresses: dict,groups:dict) -> dict:
    if set(cod_dict.keys()) != set(addresses.keys()) or set(cod_dict.keys()) != set(groups.keys()):
        raise ValueError("The keys of the two dictionaries are not the same")
    else:
        return {k: {"src": addresses[k], "group": groups[k], "data": cod_dict[k]} for k in cod_dict.keys()}


metadata=metadata[metadata["Sample_Group"]=="day 0"]
normalized_cods={k:v for k,v in normalized_cods.items() if k in metadata["Run"].to_list()}
metadata["Library Name"]=metadata["Library Name"].apply(lambda x: "-".join(x.split("-")[1:]))
metadata["src"]=metadata["Library Name"].apply(lambda x: "dsjdjs" if x=="cow" else "sndd")
addresses=dict(zip(metadata["Run"],metadata["src"]))
groups=dict(zip(metadata["Run"],metadata["Library Name"]))
with open("/Users/parsaghadermarzi/Desktop/Academics/Projects/Anaerobic_Digestion_Modeling/16s_study/full_data.json","w") as f:
    json.dump(format_for_report(normalized_cods,addresses,groups),f)

In [66]:
{k:v for k,v in normalized_cods.items() if k in metadata["Run"].to_list()}


{}

In [72]:
normalized_cods

{'SRR19159476': {'X_ch': 0.08264441768274827,
  'X_pr': 0.080495560981447,
  'X_li': 0.00219213935997678,
  'X_su': 0.07939058016584895,
  'X_aa': 0.1888015031812754,
  'X_fa': 0.1443833112252302,
  'X_ac_et': 0.06449879954273142,
  'X_ac_lac': 0.08323509867173157,
  'X_chain_et': 0.05808023586502938,
  'X_chain_lac': 0.07681653499402952,
  'X_VFA_deg': 0.0,
  'X_Me_ac': 0.0014537881237476668,
  'X_Me_CO2': 0.0019477196403974873,
  'X_et': 0.05808023586502938,
  'X_lac': 0.07798007470077678},
 'SRR19159478': {'X_ch': 0.04711639194260632,
  'X_pr': 0.07248029633951739,
  'X_li': 0.0009724745498989952,
  'X_su': 0.08279736724617309,
  'X_aa': 0.19079066601245648,
  'X_fa': 0.13569556242181524,
  'X_ac_et': 0.06939047947415648,
  'X_ac_lac': 0.088256485742197,
  'X_chain_et': 0.0682411913697304,
  'X_chain_lac': 0.0871071976377709,
  'X_VFA_deg': 0.0,
  'X_Me_ac': 0.0012951592869109346,
  'X_Me_CO2': 7.072542181083603e-05,
  'X_et': 0.0682411913697304,
  'X_lac': 0.08754481118522546},
 'S

In [67]:
metadata["Run"]

3     SRR19159475
4     SRR19159476
5     SRR19159477
6     SRR19159478
7     SRR19159479
11    SRR19159483
Name: Run, dtype: object